In [0]:
# Databricks notebook source
# DBTITLE 1,Importação de Bibliotecas
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, when

# DBTITLE 1,Criação da SparkSession
spark = SparkSession.builder.appName("CamadaGold").getOrCreate()

# DBTITLE 1,Carregar Dados da Camada Silver
inadimplencia_silver_df = spark.read.format('parquet').load('dbfs:/mnt/Aneel/Silver/inadimplencia_silver')
economicos_silver_df = spark.read.format('parquet').load('dbfs:/mnt/Aneel/Silver/economicos_silver')
dominio_indicadores_silver_df = spark.read.format('parquet').load('dbfs:/mnt/Aneel/Silver/dominio_indicadores_silver')

# Verificar dados carregados
print("Dados da Camada Silver")
display(inadimplencia_silver_df)
display(economicos_silver_df)
display(dominio_indicadores_silver_df)

# DBTITLE 1,Criar Tabelas Dimensão e Fato
# Tabela Fato de Inadimplência
fact_inadimplencia = inadimplencia_silver_df.select(
    'AnoIndice', 'SigAgente', 'SigIndicador', 'VlrIndiceEnviado', 'DatGeracaoConjuntoDados'
)
fact_inadimplencia.write.format('parquet').mode('overwrite').save('dbfs:/mnt/Aneel/Gold/fact_inadimplencia')

# Tabela Fato de Dados Econômicos
fact_economicos = economicos_silver_df.select(
    'AnoIndice', 'TaxaDesemprego', 'Inflacao', 'PIB'
)
fact_economicos.write.format('parquet').mode('overwrite').save('dbfs:/mnt/Aneel/Gold/fact_economicos')

# Tabelas Dimensão
dim_agente = inadimplencia_silver_df.select('SigAgente', 'NumCNPJ').distinct()
dim_agente.write.format('parquet').mode('overwrite').save('dbfs:/mnt/Aneel/Gold/dim_agente')

dim_indicador = dominio_indicadores_silver_df.select('SiglaIndicador', 'DescricaoIndicador').distinct()
dim_indicador.write.format('parquet').mode('overwrite').save('dbfs:/mnt/Aneel/Gold/dim_indicador')

# Dimensão Tempo usando 'AnoIndice' e 'NumPeriodoIndice'
dim_tempo = inadimplencia_silver_df.select('AnoIndice', 'NumPeriodoIndice').distinct()
dim_tempo = dim_tempo.withColumnRenamed('AnoIndice', 'Ano')
dim_tempo = dim_tempo.withColumnRenamed('NumPeriodoIndice', 'Mes')

# Calcular o trimestre a partir de 'Mes'
dim_tempo = dim_tempo.withColumn('Trimestre', 
    when(col('Mes').between(1, 3), 1)
    .when(col('Mes').between(4, 6), 2)
    .when(col('Mes').between(7, 9), 3)
    .otherwise(4)
)

dim_tempo.write.format('parquet').mode('overwrite').save('dbfs:/mnt/Aneel/Gold/dim_tempo')

# Verificar os dados das tabelas fato e dimensão
print("Tabela Dimensão Tempo")
display(dim_tempo)
print("Tabela Dimensão Agente")
display(dim_agente)
print("Tabela Dimensão Indicador")
display(dim_indicador)
print("Tabela Fato de Dados Econômicos")
display(fact_economicos)
print("Tabela Fato de Inadimplência")
display(fact_inadimplencia)


Dados da Camada Silver


DatGeracaoConjuntoDados SigAgente NumCNPJ SigIndicador AnoIndice NumPeriodoIndice VlrIndiceEnviado 2024-07-05 CEEE-D 8467115000100 IResBR21 2016 6 1.72 2024-07-05 EMR 19527639000158 IResBR21 2016 6 0.12 2024-07-05 CERPRO 44560381000139 IResBR21 2016 6 0.0 2024-07-05 CERRP 46598678000119 IResBR21 2016 6 0.0 2024-07-05 CERIM 50235449000107 IResBR21 2016 6 1.09 2024-07-05 CELESC 8336783000190 IResBR21 2016 6 1.04 2024-07-05 CERIS 57384943000182 IResBR21 2016 6 0.0 2024-07-05 CEDRAP 60196987000193 IResBR21 2016 6 2.35 2024-07-05 CETRIL 49313653000110 IResBR21 2016 6 0.21 2024-07-05 CERIPA 49606312000132 IResBR21 2016 6 0.0 2024-07-05 CERCOS 13107842000199 IResBR21 2016 6 0.13 2024-07-05 CERMOFUL 86533346000170 IResBR21 2016 6 0.0 2024-07-05 CERGRAL 86449170000173 IResBR21 2016 6 0.0 2024-07-05 CERGAPA 1229747000189 IResBR21 2016 6 0.0 2024-07-05 CEREJ 82574864000181 IResBR21 2016 6 1.08 2024-07-05 CERGAL 86439510000185 IResBR21 2016 6 0.0 2024-07-05 CERES 31465487000101 IResBR21 2016 6 0.0 2024-07-05 CEBDIS 7522669000192 IResBR21 2016 6 1.19 2024-07-05 ESS 7282377000120 IResBR21 2016 6 0.1 2024-07-05 EDEVP 7297359000111 IResBR21 2016 6 0.18 2024-07-05 COOPERMILA 75568154000183 IResBR21 2016 6 0.0 2024-07-05 CEJAMA 85665990000130 IResBR21 2016 6 0.0 2024-07-05 COOPERCOCAL 86532348000145 IResBR21 2016 6 0.0 2024-07-05 COOPERA 83646653000170 IResBR21 2016 6 0.28 2024-07-05 CERTREL 76583962000182 IResBR21 2016 6 0.0 2024-07-05 CEDRI 50105865000190 IResBR21 2016 6 17.15 2024-07-05 CERPALO 85318640000105 IResBR21 2016 6 0.0 2024-07-05 CEPRAG 78274610000170 IResBR21 2016 6 0.03 2024-07-05 CERSUL 86512670000102 IResBR21 2016 6 0.02 2024-07-05 SULGIPE 13255658000196 IResBR21 2016 6 0.36 2024-07-05 COELBA 15139629000194 IResBR21 2016 6 0.64 2024-07-05 EQUATORIAL AL 12272084000100 IResBR21 2016 6 0.04 2024-07-05 CELPE 10835932000108 IResBR21 2016 6 0.3 2024-07-05 ENEL CE 7047251000170 IResBR21 2016 6 0.58 2024-07-05 COSERN 8324196000181 IResBR21 2016 6 0.28 2024-07-05 CPFL-PAULISTA 33050196000188 IResBR21 2016 6 0.0 2024-07-05 DMED 23664303000104 IResBR21 2016 6 0.62 2024-07-05 CPFL SUL PAULIST 60855608000120 IResBR21 2016 6 0.0 2024-07-05 CPFL SANTA CRUZ 61116265000144 IResBR21 2016 6 0.0 2024-07-05 CPFL LESTE PAULI 61015582000174 IResBR21 2016 6 0.0 2024-07-05 CPFL MOCOCA 52503802000118 IResBR21 2016 6 0.0 2024-07-05 CPFL JAGUARI 53859112000169 IResBR21 2016 6 0.0 2024-07-05 CERBRANORTE 86433042000131 IResBR18 2016 6 0.0 2024-07-05 COORSEL 86448057000173 IResBR18 2016 6 0.0 2024-07-05 CERTEL ENERGIA 9257558000121 IResBR18 2016 6 0.0 2024-07-05 EQUATORIAL MA 6272793000184 IResBR21 2016 6 2.1 2024-07-05 EQUATORIAL PI 6840748000189 IResBR21 2016 6 0.0 2024-07-05 ETO 25086034000171 IResBR21 2016 6 0.11 2024-07-05 CERR 5938444000196 IResBR21 2016 6 0.0 2024-07-05 EAC 4065033000170 IResBR21 2016 6 0.0 2024-07-05 CERMC 52548732000114 IResBR18 2016 6 0.0 2024-07-05 CERNHE 53176038000186 IResBR18 2016 6 0.0 2024-07-05 EBO 8826596000195 IResBR18 2016 6 0.33 2024-07-05 Cera�� 9364804000144 IResBR18 2016 6 0.0 2024-07-05 ENF 33249046000106 IResBR18 2016 6 0.23 2024-07-05 EPB 9095183000140 IResBR18 2016 6 0.83 2024-07-05 ESE 13017462000163 IResBR18 2016 6 0.84 2024-07-05 EMR 19527639000158 IResBR18 2016 6 0.19 2024-07-05 EQUATORIAL GO 1543032000104 IResBR18 2016 6 0.4 2024-07-05 CERRP 46598678000119 IResBR18 2016 6 0.0 2024-07-05 CERIM 50235449000107 IResBR18 2016 6 0.0 2024-07-05 CEEE-D 8467115000100 IResBR18 2016 6 1.7 2024-07-05 CELESC 8336783000190 IResBR18 2016 6 1.3 2024-07-05 CERPRO 44560381000139 IResBR18 2016 6 0.0 2024-07-05 CERIS 57384943000182 IResBR18 2016 6 0.0 2024-07-05 CEDRAP 60196987000193 IResBR18 2016 6 0.0 2024-07-05 CETRIL 49313653000110 IResBR18 2016 6 0.19 2024-07-05 CERIPA 49606312000132 IResBR18 2016 6 0.0 2024-07-05 EMS 15413826000150 IResBR21 2016 6 1.12 2024-07-05 EMT 3467321000199 IResBR21 2016 6 0.39 2024-07-05 COPREL 90660754000160 IResBR21 2016 6 0.34 2024-07-05 CRELUZ-D 91950261000128 IResBR21 2016 6 0.0 2024-07-05 MUX

AnoIndice TaxaDesemprego Inflacao PIB 2012 7.4 344.4 4.8147601E12 2013 7.3 365.8 5.3316189E12 2014 6.9 388.9 5.7789529E12 2015 8.4 424.0 5.9957869E12 2016 11.4 461.1 6.2693279E12 2017 12.9 477.0 6.5854788E12 2018 12.4 494.5 7.0041411E12 2019 12.1 512.9 7.389131E12 2020 13.5 529.4 7.6095968E12 2021 13.5 573.3 9.0121416E12 2022 9.5 627.5 1.00796769E13 2023 8.0 655.3 1.08561118E13

SiglaIndicador DescricaoIndicador AREA Área do conj., expressa em km2, correspondente a área geogr. e não a área elétr. AREAT Área do conjunto em km2 CM Encargo de uso do sistema de distribuição aplicado à unidade cons. (mensal) CMA Encargo de uso do sistema de distribuição aplicado à unidade consumidora (anual) CMM Consumo médio mensal, em MWh, média aritmética simples do último ano, excluin- CMMT Consumo médio mensal em MWh CMMTCO Energia cons comercial nos últimos 12 meses (ano móvel) MT e BT CMMTIN Energia cons industrial nos últimos 12 meses (ano móvel) MT e BT CMMTOU Energia cons outras classes nos últimos 12 meses (ano móvel) MT e BT CMMTRE Energia cons residencial nos últimos 12 meses (ano móvel) MT e BT CMMTRU Energia cons rural nos últimos 12 meses (ano móvel) MT e BT CMT Encargo de uso do sistema de distribuição aplicado à unidade cons. (trimestral) CODCLSUC Código da Classe da Unidade Consumidora CODCLSUCA Código da Classe da Unidade Consumidora CODCLSUCT Código da Classe da Unidade Consumidora CODMUNUC Código do Munícipio do Consumidor CODMUNUCA Código do Munícipio do Consumidor CODMUNUCT Código do Munícipio do Consumidor COMPCONF Compensação de UC atendida fora dos limites previstos de DRP ou DRC COMPCONT Compensação pela violação do DIC, FIC ou DMIC COMPCONTA Compensação pela violação do DIC, FIC ou DMIC COMPCONTT Compensação pela violação do DIC, FIC ou DMIC CRAfedMed Créd. Prazo Viol. de solicitações de aferição dos medidores (art. 137) CRAnProj Créd. Prazo Viol. de informação do resultado da análise do projeto (art. 27-B) CRCmsnObra Créd. Prazo Viol. de Comissionamento das obras. (art. 37) CREstProj Créd. Prazo Viol. por estudos, orçamentos e projetos por obras (art. 32) CRInform Créd. Prazo Viol. de informação da relação dos atendimentos (art. 199) CRLigA Créd. Prazo Viol. por ligação de unidade consumidora do grupo A (art. 31) CRLigBRr Créditos cedidos por ligação de consumidor do grupo B em área rural (art. 31) CRLigBUb Créd. Prazo Viol. por ligação de consumidor do grupo B em área urbana (art. 31) CRNvCmsn Créd. Prazo Viol. de Novo comissionamento quando de reprovação. (art. 37) CRObGerais Créd. Prazo Viol. de Conclusão de obra não abrang. nos inc. I e II do art. 34. CRObra Créd. Prazo Viol. por Início das Obras (art. 34) CRObraPrim Créd. Prazo Viol. de Conclusão das obras de até 1 km na rede prim. (art. 34) CRObraSec Créd. Prazo Viol. de Conclusão das obras na rede tensão secundária. (art. 34) CRPgtoRsc Créd. Prazo Viol. de ressarc. por meio do pgto, conserto ou subst. (art. 208) CRRclCobr Créd. Prazo Viol. de reclamação de cobrança ou devol. de diferenças (art. 133) CRRclDano Créd. Prazo Viol. de solução ref. à danos não elétricos reclamados (art. 197) CRRclVisTc Créd. Prazo Viol. de solução de reclamação com visita técnica (art. 197) CRReanProj Créd. Prazo Viol. de reanálise do projeto por falta de informação (art. 27-B) CRReligIdv Créd. Prazo Viol. de religação por suspensão indevida do fornec. (art. 176) CRRelNorRr Créd. Prazo Viol. de religação em área rural (art. 176) CRRelNorUb Créd. Prazo Viol. de religação em área urbana (art. 176) CRRelUrgRr Créd. Prazo Viol. de religação de emergência em área rural (art. 176) CRRelUrgUb Créd. Prazo Viol. de religação de emergência em área urbana (art. 176) CRResulRsc Créd. Prazo Viol. de resultado da solicitação de ressarcimento (art. 207) CRSubstMed Créditos cedidos por substituição do medidor com defeito (art. 115) CRVistRr Créd. Prazo Viol. por vistoria de unidade consumidora de área rural (art. 30) CRVistUb Créd. Prazo Viol. por vistoria de unidade consumidora de área urbana (art. 30) CRVrfResfr Créd. Prazo Viol. de verif. de equip. de resfriamento por ressarc. (art. 206) CRVrfRsc Créd. Prazo Viol. de verif. de equip. por ressarc. de dano elétrico (art. 206) DEC Duração Equivalente de Interrupção por Unidade Consumidora - 3 Min. Dec1 Duração Equivalente de Interrupção por Unidade Consumidora - 1 Min. DEC1i Duração Equivalente de Interrupção por Unid. Cons.

Tabela Dimensão Tempo


...

SiglaIndicador DescricaoIndicador DMICVLDA Valor apurado do indicador DMIC violado Fec1r Freqüência Equivalente de Interrupção por Unidade Consumidora (Racion.)- 1 Min. IRur6 Perc. da rec. fat. 6° mês ant. não receb. no mês de ref. classe Rural CREstProj Créd. Prazo Viol. por estudos, orçamentos e projetos por obras (art. 32) TI1 Tensão Interna QVRclCobr Quant. Prazos Viol. de reclamação de cobrança ou devol. de diferenças (art. 133) QVReligIdv Quant. Prazos Viol. de religação por suspensão indevida do fornec. (art. 176) NMOPTP Número de mortes de decorrentes de acidentes do trabalho - Próprio Típico PMVrfRsc Prazo Médio de verif. de equip. por ressarc. de dano elétrico (art. 206) NEMPRT Números de Empregados - Terceirizado QSVistRr Quantidade de vistoria de unidade consumidora de área rural (art. 30) QTUCMTNU Qtde de UCs MT não urbanas comp por violacao dos limites de cont no mes CMM Consumo médio mensal, em MWh, média aritmética simples do último ano, excluin- CODCLSUCT Código da Classe da Unidade Consumidora COMPCONTT Compensação pela violação do DIC, FIC ou DMIC FECXP FEC de interrupção de origem externa ao Sist. de Dist. e programada ICProp1 Perc. da rec. fat. 1° mês ant. não receb. no mês de ref. classe Consumo Próp. ISerPub6 Perc. da rec. fat. 6° mês ant. não receb. no mês de ref. classe Serviço Púb. QVLigBRr Quant. Prazos Viol. de ligação de consumidor do grupo B em área rural (art. 31) NMOTTJ Número de mortes de decorrentes de acidentes do trabalho - Terceirizado Trajeto NumCon Número de Consumidores do Conjunto no Período PGUCTRPP Valor pago a UCs por violação limites de tensão em regime permmed.amostral TSCT Tipo de sistema do conjunto. 1: Interligado, 2: Isolado PGUCMTUDC Valor pago as UCs MT urbanas por violacao dos limites de DICRI QSVrfResfr Quantidade de verif. de equip. de resfriamento por ressarc. (art. 206) QTUCTRPA Qtde de UC compens.-violação limites de tensão em regime permmed.amostral CODMUNUCA Código do Munícipio do Consumidor DIADEBTTP Dias Debitados - Terceirizado Típico PMLigA Prazo Médio de ligação de unidade consumidora do grupo A (art. 31) QVInform Quant. Prazos Viol. de informação da relação dos atendimentos (art. 199) QTUGMTU Qtde de UGs MT urbanas compensadas por violacao dos limites de cont no mes IResBR3 Perc. da rec. fat. 3° mês ant. não receb. no mês de ref. classe Resid. Baixa R. PGUCATA Valor pago a UCs AT por violacao dos limites de cont no ano PMObGerais Prazo médio de Conclusão de obra não abrang. nos inc. I e II do art. 34. FQACCATTP Taxa de frequência de acidentados com lesão com afastamento - Terceiri ITot21 Perc. da rec. fat. 21° mês ant. não receb. no mês de ref. todos os consumidores NACTTJ Número de acidentes do trabalho - Terceirizado Trajeto QTUGBTUA Qtde de UGs BT urbanas compens por violacao dos limites de cont no ano ICom18 Perc. da rec. fat. 18° mês ant. não receb. no mês de ref. classe Comercial Pnie Percentual do Número de Ocorreências Emergenciais com Interrupções FQACCAPTP Taxa de frequência de acidentados com lesão com afastamento - Próprio GRVACTTP Taxa de gravidade de acidentes do trabalho - Terceirizado Típico QVCmsnObra Quant. Prazos Viol. de Comissionamento das obras. (art. 37) QTUCBTNUDC Qtde de UCs BT não urbanas comp por violacao dos limites de DICRI DECIND DEC interrup origem interna, não programada e não expurgavel NACTERCHO Nº acid terc rede e demais instal - Choque elétrico por contato QVPgtoRsc Quant. Prazos Viol. de ressarc. por meio do pgto, conserto ou subst. (art. 208) QSObraPrim Quantidade de Conclusão das obras de até 1 km na rede prim. (art. 34) PNIT Potência instalada de transformadores de distribuição, em kVA, de todos os NACTEROUT Nº acid terc rede e demais instal - Outros. TXGRAC Taxa de gravidade de acidentes do trabalho CRAfedMed Créd. Prazo Viol. de solicitações de aferição dos medidores (art. 137) CRLigA Créd. Prazo Viol. por ligação de unidade consumidora do grupo A (art. 31) IRestot24 Perc. da rec. fat. 24° mês ant. não receb. no mês de

Tabela Fato de Dados Econômicos


AnoIndice TaxaDesemprego Inflacao PIB 2012 7.4 344.4 4.8147601E12 2013 7.3 365.8 5.3316189E12 2014 6.9 388.9 5.7789529E12 2015 8.4 424.0 5.9957869E12 2016 11.4 461.1 6.2693279E12 2017 12.9 477.0 6.5854788E12 2018 12.4 494.5 7.0041411E12 2019 12.1 512.9 7.389131E12 2020 13.5 529.4 7.6095968E12 2021 13.5 573.3 9.0121416E12 2022 9.5 627.5 1.00796769E13 2023 8.0 655.3 1.08561118E13

Tabela Fato de Inadimplência


AnoIndice SigAgente SigIndicador VlrIndiceEnviado DatGeracaoConjuntoDados 2016 CEEE-D IResBR21 1.72 2024-07-05 2016 EMR IResBR21 0.12 2024-07-05 2016 CERPRO IResBR21 0.0 2024-07-05 2016 CERRP IResBR21 0.0 2024-07-05 2016 CERIM IResBR21 1.09 2024-07-05 2016 CELESC IResBR21 1.04 2024-07-05 2016 CERIS IResBR21 0.0 2024-07-05 2016 CEDRAP IResBR21 2.35 2024-07-05 2016 CETRIL IResBR21 0.21 2024-07-05 2016 CERIPA IResBR21 0.0 2024-07-05 2016 CERCOS IResBR21 0.13 2024-07-05 2016 CERMOFUL IResBR21 0.0 2024-07-05 2016 CERGRAL IResBR21 0.0 2024-07-05 2016 CERGAPA IResBR21 0.0 2024-07-05 2016 CEREJ IResBR21 1.08 2024-07-05 2016 CERGAL IResBR21 0.0 2024-07-05 2016 CERES IResBR21 0.0 2024-07-05 2016 CEBDIS IResBR21 1.19 2024-07-05 2016 ESS IResBR21 0.1 2024-07-05 2016 EDEVP IResBR21 0.18 2024-07-05 2016 COOPERMILA IResBR21 0.0 2024-07-05 2016 CEJAMA IResBR21 0.0 2024-07-05 2016 COOPERCOCAL IResBR21 0.0 2024-07-05 2016 COOPERA IResBR21 0.28 2024-07-05 2016 CERTREL IResBR21 0.0 2024-07-05 2016 CEDRI IResBR21 17.15 2024-07-05 2016 CERPALO IResBR21 0.0 2024-07-05 2016 CEPRAG IResBR21 0.03 2024-07-05 2016 CERSUL IResBR21 0.02 2024-07-05 2016 SULGIPE IResBR21 0.36 2024-07-05 2016 COELBA IResBR21 0.64 2024-07-05 2016 EQUATORIAL AL IResBR21 0.04 2024-07-05 2016 CELPE IResBR21 0.3 2024-07-05 2016 ENEL CE IResBR21 0.58 2024-07-05 2016 COSERN IResBR21 0.28 2024-07-05 2016 CPFL-PAULISTA IResBR21 0.0 2024-07-05 2016 DMED IResBR21 0.62 2024-07-05 2016 CPFL SUL PAULIST IResBR21 0.0 2024-07-05 2016 CPFL SANTA CRUZ IResBR21 0.0 2024-07-05 2016 CPFL LESTE PAULI IResBR21 0.0 2024-07-05 2016 CPFL MOCOCA IResBR21 0.0 2024-07-05 2016 CPFL JAGUARI IResBR21 0.0 2024-07-05 2016 CERBRANORTE IResBR18 0.0 2024-07-05 2016 COORSEL IResBR18 0.0 2024-07-05 2016 CERTEL ENERGIA IResBR18 0.0 2024-07-05 2016 EQUATORIAL MA IResBR21 2.1 2024-07-05 2016 EQUATORIAL PI IResBR21 0.0 2024-07-05 2016 ETO IResBR21 0.11 2024-07-05 2016 CERR IResBR21 0.0 2024-07-05 2016 EAC IResBR21 0.0 2024-07-05 2016 CERMC IResBR18 0.0 2024-07-05 2016 CERNHE IResBR18 0.0 2024-07-05 2016 EBO IResBR18 0.33 2024-07-05 2016 Cera�� IResBR18 0.0 2024-07-05 2016 ENF IResBR18 0.23 2024-07-05 2016 EPB IResBR18 0.83 2024-07-05 2016 ESE IResBR18 0.84 2024-07-05 2016 EMR IResBR18 0.19 2024-07-05 2016 EQUATORIAL GO IResBR18 0.4 2024-07-05 2016 CERRP IResBR18 0.0 2024-07-05 2016 CERIM IResBR18 0.0 2024-07-05 2016 CEEE-D IResBR18 1.7 2024-07-05 2016 CELESC IResBR18 1.3 2024-07-05 2016 CERPRO IResBR18 0.0 2024-07-05 2016 CERIS IResBR18 0.0 2024-07-05 2016 CEDRAP IResBR18 0.0 2024-07-05 2016 CETRIL IResBR18 0.19 2024-07-05 2016 CERIPA IResBR18 0.0 2024-07-05 2016 EMS IResBR21 1.12 2024-07-05 2016 EMT IResBR21 0.39 2024-07-05 2016 COPREL IResBR21 0.34 2024-07-05 2016 CRELUZ-D IResBR21 0.0 2024-07-05 2016 MUXENERGIA IResBR21 0.07 2024-07-05 2016 UHENPAL IResBR21 0.48 2024-07-05 2016 HIDROPAN IResBR21 0.06 2024-07-05 2016 ELETROCAR IResBR21 0.59 2024-07-05 2016 RGE IResBR21 0.0 2024-07-05 2016 COOPERALIAN�A IResBR21 0.55 2024-07-05 2016 COPEL-DIS IResBR21 0.63 2024-07-05 2016 CRERAL IResBR21 0.0 2024-07-05 2016 CERILUZ IResBR21 0.0 2024-07-05 2016 CERMISS�ES IResBR21 0.07 2024-07-05 2016 CERTAJA IResBR21 0.0 2024-07-05 2016 CPFL-PIRATINING IResBR21 0.0 2024-07-05 2016 COOPERLUZ IResBR21 0.0 2024-07-05 2016 CERAL-DIS IResBR21 0.0 2024-07-05 2016 CEMIG-D IResBR21 2.06 2024-07-05 2016 BOA VISTA IResBR21 0.0 2024-07-05 2016 CHESP IResBR21 0.0 2024-07-05 2016 CERON IResBR21 0.0 2024-07-05 2016 DEMEI IResBR21 0.38 2024-07-05 2016 EFLJC IResBR21 0.0 2024-07-05 2016 EFLUL IResBR21 0.0 2024-07-05 2016 DCELT IResBR21 0.22 2024-07-05 2016 CNEE IResBR21 0.11 2024-07-05 2016 COCEL IResBR21 0.31 2024-07-05 2016 PACTO ENERGIA PR IResBR21 0.0 2024-07-05 2016 CFLO IResBR21 0.12 2024-07-05 2016 RGE SUL IResBR21 0.98 2024-07-05 2016 EDP SP IResBR21 2.55 2024-07-05 2016 ELETROPAULO IResBR21 6.83 2024-07-05 2016 EEB IResBR21 0.07 2024-07-05 2016 ELEKTRO IResBR21 0.0 2024-07-05 2016 EQUATORIAL PA IResBR21 4.3 2024-07-05 2016 EDP ES IResBR21 4